In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objs as go
import plotly.offline as py
from fbprophet import Prophet
from fbprophet.plot import plot_plotly, add_changepoints_to_plot
import streamlit as st
py.init_notebook_mode()
import yfinance as yfinance

In [3]:
import pandas_datareader as web
ticker = pd.read_csv('./dataset/nasdaq_nyse_energy.csv')['Symbol']
df = pd.DataFrame
df = web.DataReader(ticker,'yahoo', start= '2017-06-01',end= '2022-07-01')['Adj Close']
             
                                           
        
        
df

Symbols           ABB        APA        BKR         BP        CLR        COP  \
Date                                                                           
2017-06-01  21.215113  42.684917  33.277672  26.959341  36.937241  38.837337   
2017-06-02  21.694407  42.405163  32.930096  26.713850  35.200169  38.317886   
2017-06-05  21.467373  42.170528  32.798248  26.840307  35.209930  38.110111   
2017-06-06  21.475782  43.352711  33.319618  26.959341  35.893051  38.508362   
2017-06-07  21.273973  42.215652  32.528580  26.349331  34.204765  37.711880   
...               ...        ...        ...        ...        ...        ...   
2022-06-27  27.100000  37.336178  29.440001  28.700001  67.279999  92.230003   
2022-06-28  26.870001  38.631535  30.070000  29.070000  67.690002  95.220001   
2022-06-29  26.879999  35.971069  29.629999  28.770000  66.250000  91.459999   
2022-06-30  26.730000  34.775356  28.870001  28.350000  65.349998  89.809998   
2022-07-01  26.610001  35.223747  29.090000  28.280001  65.660004  90.980003   

Symbols          CTRA         CVX        DVN          E  ...         PXD  \
Date                                                     ...               
2017-06-01  19.013512   83.525261  28.594629  23.841593  ...  148.084778   
2017-06-02  18.532812   82.596077  27.643431  23.655680  ...  146.231186   
2017-06-05  18.455549   82.660141  27.576668  23.521822  ...  146.789886   
2017-06-06  18.884754   83.445183  28.285906  23.811846  ...  149.628006   
2017-06-07  18.970592   83.124748  26.633806  23.246670  ...  146.302109   
...               ...         ...        ...        ...  ...         ...   
2022-06-27  27.030001  147.570007  57.790001  24.160000  ...  230.169998   
2022-06-28  27.690001  149.940002  59.459999  24.230000  ...  235.330002   
2022-06-29  26.709999  146.979996  55.820000  24.170000  ...  226.179993   
2022-06-30  25.790001  144.779999  55.110001  23.809999  ...  223.080002   
2022-07-01  26.330000  146.509995  55.110001  23.719999  ...  223.940002   

Symbols          SHEL        SLB        SNP        SSL          TPL  \
Date                                                                  
2017-06-01  42.518642  59.341663  50.837456  27.983164   257.936401   
2017-06-02  42.143829  58.644333  50.751595  28.274851   264.813324   
2017-06-05  42.346851  58.907955  50.665749  28.237213   262.625641   
2017-06-06  42.463982  59.503250  50.960094  28.227806   265.837921   
2017-06-07  41.940788  58.397720  50.763855  27.776159   263.484070   
...               ...        ...        ...        ...          ...   
2022-06-27  51.840000  35.889999  44.959999  23.320000  1538.640015   
2022-06-28  53.150002  36.970001  45.820000  22.920000  1632.739990   
2022-06-29  52.599998  36.180000  45.220001  23.230000  1505.790039   
2022-06-30  52.290001  35.759998  44.790001  23.059999  1488.020020   
2022-07-01  51.900002  35.650002  45.139999  21.680000  1526.969971   

Symbols           TTE         VLO        WDS        XOM  
Date                                                     
2017-06-01  38.385059   49.345909  19.541908  61.977139  
2017-06-02  38.466095   49.330021  19.649462  61.055542  
2017-06-05  38.134552   49.568333  19.657738  61.531708  
2017-06-06  38.259808   49.480946  19.649462  62.368816  
2017-06-07  37.699867   49.488892  19.475721  62.138435  
...               ...         ...        ...        ...  
2022-06-27  52.730000  112.239998  21.809999  89.029999  
2022-06-28  53.299999  116.250000  22.469999  91.500000  
2022-06-29  52.970001  108.849998  22.120001  88.120003  
2022-06-30  52.639999  106.279999  21.559999  85.639999  
2022-07-01  52.830002  107.980003  20.879999  87.550003  

[1281 rows x 37 columns]

In [4]:
df.to_csv('./nasdaq_nyse_energy_hist.csv')

# Data Preprocessing

In [5]:
figure = pd.read_csv('nasdaq_nyse_energy_hist.csv')
figure.head()

Date        ABB        APA        BKR         BP        CLR  \
0  2017-06-01  21.215113  42.684917  33.277672  26.959341  36.937241   
1  2017-06-02  21.694407  42.405163  32.930096  26.713850  35.200169   
2  2017-06-05  21.467373  42.170528  32.798248  26.840307  35.209930   
3  2017-06-06  21.475782  43.352711  33.319618  26.959341  35.893051   
4  2017-06-07  21.273973  42.215652  32.528580  26.349331  34.204765   

         COP       CTRA        CVX        DVN  ...         PXD       SHEL  \
0  38.837337  19.013512  83.525261  28.594629  ...  148.084778  42.518642   
1  38.317886  18.532812  82.596077  27.643431  ...  146.231186  42.143829   
2  38.110111  18.455549  82.660141  27.576668  ...  146.789886  42.346851   
3  38.508362  18.884754  83.445183  28.285906  ...  149.628006  42.463982   
4  37.711880  18.970592  83.124748  26.633806  ...  146.302109  41.940788   

         SLB        SNP        SSL         TPL        TTE        VLO  \
0  59.341663  50.837456  27.983164  257.936401  38.385059  49.345909   
1  58.644333  50.751595  28.274851  264.813324  38.466095  49.330021   
2  58.907955  50.665749  28.237213  262.625641  38.134552  49.568333   
3  59.503250  50.960094  28.227806  265.837921  38.259808  49.480946   
4  58.397720  50.763855  27.776159  263.484070  37.699867  49.488892   

         WDS        XOM  
0  19.541908  61.977139  
1  19.649462  61.055542  
2  19.657738  61.531708  
3  19.649462  62.368816  
4  19.475721  62.138435  

[5 rows x 38 columns]

In [6]:

# Visualizing The Price of the stocks
# to set the plot size
plt.figure(figsize=(16, 8), dpi=150)
  
# using .plot method to plot stock prices.
# we have passed colors as a list
figure.plot(label='ABB', color=['orange', 'green'])
  
# adding title
plt.title('Price Plot')
  
# adding label to x-axis
plt.xlabel('Days')
  
# adding legend.
plt.legend()

NameError: name 'plt' is not defined

In [9]:
import plotly.express as px
df = px.data.stocks()
fig = px.line(figure, x="Date", y=figure.columns,
             hover_data={"Date": "|%B %d, %Y"},
              title='custom tick labels')
fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

# Automatic Portfolio Optimization

In [3]:
#df = pd.read_csv('nasdaqtechend.csv')
from sua import EfficientFrontier
from sua import risk_models
from sua import expected_returns

# Calculate the expected annual returns and the annulized sample covariance matrix of the daily asset  returns

mu = expected_returns.mean_historical_return(df)
S = risk_models.sample_cov(df)


In [4]:
#from pypfopt import objective_functions, base_optimizer
ef = EfficientFrontier(mu, S)
#ef.add_objective(objective_functions.L2_reg, gamma=2)
weights= ef.max_sharpe()
#weights = ef.nonconvex_objective(
       #objective_functions.sharpe_ratio,
       #objective_args=(ef.expected_returns, ef.cov_matrix),
       #weights_sum_to_one=True,

    #)
cleaned_weights = ef.clean_weights()
print(cleaned_weights)
ef.portfolio_performance(verbose=True)

OrderedDict([('ABB', 0.0), ('APA', 0.0), ('BKR', 0.0), ('BP', 0.0), ('CLR', 0.0), ('COP', 0.0), ('CTRA', 0.0), ('CVX', 0.0), ('DVN', 0.0), ('E', 0.0), ('EC', 0.0), ('ENB', 0.0), ('EOG', 0.0), ('EQNR', 0.08433), ('EQT', 0.0), ('FANG', 0.0), ('HAL', 0.0), ('HES', 0.0), ('MPC', 0.0), ('MPLX', 0.0), ('MRO', 0.0), ('OVV', 0.0), ('OXY', 0.0), ('PBA', 0.0), ('PBR', 0.0), ('PSX', 0.0), ('PTR', 0.0), ('PXD', 0.0), ('SHEL', 0.0), ('SLB', 0.0), ('SNP', 0.0), ('SSL', 0.0), ('TPL', 0.91567), ('TTE', 0.0), ('VLO', 0.0), ('WDS', 0.0), ('XOM', 0.0)])
Expected annual return: 39.5%
Annual volatility: 47.0%
Sharpe Ratio: 0.80


(0.39488621033349086, 0.4698837437981395, 0.7978275802930112)

In [12]:
from pypfopt.discrete_allocation import DiscreteAllocation, get_latest_prices

#Portfolio value defines the budget amount
portfolio_val = 30000

latest_prices = get_latest_prices(df) # By getting recent price for the automated protfolio, it will help to allocate certain amounts
weights = cleaned_weights
da = DiscreteAllocation(weights, latest_prices, total_portfolio_value = portfolio_val)
allocation, leftover = da.lp_portfolio(reinvest=True ,verbose = True)
print('Discrete allocation:', allocation)
print('Funds remaining: $', leftover)

C:\Users\manne\anaconda3\lib\site-packages\cvxpy\problems\problem.py:1337: UserWarning:

Solution may be inaccurate. Try another solver, adjusting the solver settings, or solve with verbose=True for more information.



OptimizationError: ('Please check your objectives/constraints or use a different solver.', 'Please try greedy_portfolio')

In [ ]:
!pip list